
### Project: Adversarial De-identification of Clinical Text Using Synthetic MIMIC-III Data

This script implements a pipeline to protect sensitive information in clinical notes
via adversarial perturbations. It leverages a synthetic MIMIC-III dataset and a pre-trained
BioBERT model for token classification. Sensitive entities (dates and names) are detected
and perturbed: date tokens are replaced with synthetic dates while name tokens have some
random letters substituted. The utility and privacy risks of the perturbations are then evaluated.

Usage:
    Run this script from the command line. Ensure that the synthetic dataset
    (synthetic_NOTEEVENTS_random.csv) is available in the "data/" folder.

Dependencies:
    - torch
    - transformers
    - nltk
    - pandas
    - scikit-learn


In [25]:
%pip install torch transformers nltk

Note: you may need to restart the kernel to use updated packages.


In [26]:
import re
import random
import pandas as pd
import nltk
from transformers import AutoTokenizer, AutoModelForTokenClassification, pipeline
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to /Users/areef/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

In [27]:
# -----------------------------------------------------------------------------
# Module 1: Data Loading and Preprocessing
# -----------------------------------------------------------------------------
def load_data(file_path: str) -> pd.DataFrame:
    """
    Loads the synthetic MIMIC-III dataset from a CSV file.
    
    Args:
      file_path (str): Path to the synthetic data CSV file.
    
    Returns:
      pd.DataFrame: Loaded DataFrame.
    """
    try:
        df = pd.read_csv(file_path, dtype={4: str, 5: str})
        print("Number of notes loaded:", len(df))
        # print("Sample note:\n", df['SYNTHETIC_TEXT'].iloc[0])
        return df
    except Exception as e:
        print("Error loading dataset:", e)
        exit(1)

def preprocess_text(text: str) -> str:
    """
    Removes de-identification placeholder brackets while keeping the inner content.
    
    Args:
        text (str): The original clinical note text.
        
    Returns:
        str: Preprocessed text without placeholder markers.
    """
    def replace_placeholder(match):
        return match.group(1)
    
    cleaned_text = re.sub(r"\[\*\*([^\]]*)\*\*\]", replace_placeholder, text)
    return cleaned_text.strip()

def preprocess_dataframe(df: pd.DataFrame, text_column: str = "SYNTHETIC_TEXT") -> pd.DataFrame:
    """
    Applies preprocessing to a DataFrame containing clinical notes.
    
    Args:
        df (pd.DataFrame): The input DataFrame.
        text_column (str): Column name containing the text.
        
    Returns:
        pd.DataFrame: DataFrame with an added "TEXT_PRE" column.
    """
    df['TEXT_PRE'] = df[text_column].apply(preprocess_text)
    # print("\nPreprocessed text snippet:")
    # print(df['TEXT_PRE'].iloc[0][:500])
    return df

In [28]:
# -----------------------------------------------------------------------------
# Module 2: Sentence-Based Chunking with Offsets and Sensitive Entity Detection
# -----------------------------------------------------------------------------
def chunk_text_with_offsets(text: str, tokenizer, max_length: int = 512) -> list:
    """
    Splits the full text into chunks based on sentence boundaries.
    Each chunk is built by concatenating sentences until adding another would
    exceed max_length tokens (including special tokens). If a chunk is too long,
    it is split further by words.
    
    Returns:
      List of tuples: (chunk_text, start_offset, end_offset) from the original text.
    """
    # Use PunktSentenceTokenizer to obtain sentence spans.
    punkt_tokenizer = nltk.tokenize.PunktSentenceTokenizer()
    spans = list(punkt_tokenizer.span_tokenize(text))
    
    chunks = []
    current_chunk = ""
    current_start = None
    current_end = None
    for span in spans:
        sentence = text[span[0]:span[1]].strip()
        if not sentence:
            continue
        if current_chunk == "":
            current_chunk = sentence
            current_start, current_end = span
        else:
            candidate = current_chunk + " " + sentence
            token_count = len(tokenizer.encode(candidate, add_special_tokens=True))
            if token_count <= max_length:
                current_chunk = candidate
                current_end = span[1]
            else:
                chunks.append((current_chunk, current_start, current_end))
                current_chunk = sentence
                current_start, current_end = span
    if current_chunk:
        chunks.append((current_chunk, current_start, current_end))
    
    # For any chunk that exceeds max_length, split by words.
    final_chunks = []
    for chunk_text, start_offset, end_offset in chunks:
        token_count = len(tokenizer.encode(chunk_text, add_special_tokens=True))
        if token_count <= max_length:
            final_chunks.append((chunk_text, start_offset, end_offset))
        else:
            words = chunk_text.split()
            sub_chunk = ""
            sub_start = None
            for word in words:
                candidate = sub_chunk + (" " if sub_chunk else "") + word
                if sub_chunk == "":
                    sub_start = text.find(word, start_offset, end_offset)
                token_count = len(tokenizer.encode(candidate, add_special_tokens=True))
                if token_count <= max_length:
                    sub_chunk = candidate
                else:
                    sub_end = text.find(word, start_offset, end_offset)
                    final_chunks.append((sub_chunk, sub_start, sub_end))
                    sub_chunk = word
                    sub_start = text.find(word, start_offset, end_offset)
            if sub_chunk:
                final_chunks.append((sub_chunk, sub_start, end_offset))
    return final_chunks

def detect_sensitive_entities(text: str, ner_model, tokenizer) -> list:
    """
    Detects sensitive entities using the NER pipeline.
    Offsets from each chunk are adjusted to full-text offsets.
    """
    chunks = chunk_text_with_offsets(text, tokenizer, max_length=512)
    detected_entities = []
    ner_pipe = pipeline("ner", model=ner_model, tokenizer=tokenizer, aggregation_strategy="simple")
    for chunk_text, chunk_start, _ in chunks:
        predictions = ner_pipe(chunk_text)
        for pred in predictions:
            pred["start"] += chunk_start
            pred["end"] += chunk_start
            detected_entities.append(pred)
    return detected_entities

def debug_ner_pipeline(text: str, ner_model, tokenizer, max_length=512):
    """
    Splits the text into chunks with offsets and prints NER predictions.
    """
    chunks = chunk_text_with_offsets(text, tokenizer, max_length=max_length)
    print("======= DEBUG: NER Pipeline =======")
    print(f"Total chunks: {len(chunks)}\n")
    all_predictions = []
    ner_pipe = pipeline("ner", model=ner_model, tokenizer=tokenizer, aggregation_strategy="simple")
    for idx, (chunk_text, start_offset, _) in enumerate(chunks, start=1):
        print(f"--- Chunk {idx} (Start Offset: {start_offset}) ---")
        print("CHUNK TEXT:\n", chunk_text[:500], "\n")
        preds = ner_pipe(chunk_text)
        for p in preds:
            p["start"] += start_offset
            p["end"] += start_offset
            print(f"Label={p.get('entity_group')}, Word='{p.get('word')}', Span=({p.get('start')}, {p.get('end')})")
        print()
        all_predictions.extend(preds)
    print("======= END DEBUG =======")
    return all_predictions

In [29]:
# -----------------------------------------------------------------------------
# Module 3: Offset-Based Perturbation Functions for Sensitive Tokens
# -----------------------------------------------------------------------------
def random_letter_perturbation(token: str, rate: float = 0.3) -> str:
    """
    Randomly perturbs letters in a token with a specified probability.
    """
    letters = list(token)
    for i in range(len(letters)):
        if letters[i].isalpha() and random.random() < rate:
            letters[i] = random.choice("ABCDEFGHIJKLMNOPQRSTUVWXYZ" if letters[i].isupper() else "abcdefghijklmnopqrstuvwxyz")
    return "".join(letters)

def perturb_text_offsets(text: str, ner_model, tokenizer, fake_dates=None, rate: float = 0.3) -> str:
    """
    Uses the NER pipeline to detect sensitive entities and replaces only those spans
    using full-text offsets. The new text is rebuilt in one pass.
    
    Args:
      text (str): Original clinical note.
      ner_model: Trained NER model.
      tokenizer: Corresponding tokenizer.
      fake_dates (list, optional): Synthetic dates list.
      rate (float, optional): Perturbation rate.
    
    Returns:
      str: Perturbed text.
    """
    if fake_dates is None:
        fake_dates = ["2188-12-01", "2189-03-15", "2189-06-20", "2188-09-10"]
    
    predictions = detect_sensitive_entities(text, ner_model, tokenizer)
    # print("\n=== DEBUG: Detected Entities (Full Offsets) ===")
    # for p in predictions:
    #     print(f"Label={p.get('entity_group')}, Word='{p.get('word')}', Span=({p.get('start')}, {p.get('end')})")
    # print("=== END DEBUG ===\n")
    
    # Sort predictions by start offset (increasing order)
    predictions_sorted = sorted(predictions, key=lambda x: x["start"])
    new_text_parts = []
    prev_end = 0
    for pred in predictions_sorted:
        start = pred["start"]
        end = pred["end"]
        label = pred.get("entity_group", "").upper()
        entity = text[start:end]
        if not entity:
            continue
        # Append text between the previous prediction and current.
        new_text_parts.append(text[prev_end:start])
        # Replace sensitive span based on label.
        if label == "DATE" or re.match(r"^\d{4}-\d{1,2}-\d{1,2}(?:\s+\d{1,2}:\d{2})?$", entity.replace(" ", "")):
            new_date = random.choice(fake_dates)
            if entity.split()[0] == new_date:
                candidates = [d for d in fake_dates if d != new_date]
                new_date = random.choice(candidates) if candidates else new_date
            replacement = new_date
        else:
            tokens = entity.split()
            perturbed_tokens = [random_letter_perturbation(tok, rate=rate) for tok in tokens]
            replacement = " ".join(perturbed_tokens)
        new_text_parts.append(replacement)
        prev_end = end
    new_text_parts.append(text[prev_end:])
    return "".join(new_text_parts)

In [30]:
# -----------------------------------------------------------------------------
# Module 4: Evaluation Functions
# -----------------------------------------------------------------------------
def evaluate_text_similarity(original_text: str, perturbed_text: str, vectorizer: TfidfVectorizer) -> tuple:
    """
    Computes BLEU score and cosine similarity between original and perturbed texts.
    """
    try:
        orig_tokens = nltk.word_tokenize(original_text)
        pert_tokens = nltk.word_tokenize(perturbed_text)
        bleu_score = nltk.translate.bleu_score.sentence_bleu([orig_tokens], pert_tokens)
    except Exception as e:
        print(f"⚠️ BLEU score calculation failed: {str(e)}")
        bleu_score = 0.0

    try:
        vecs = vectorizer.fit_transform([original_text, perturbed_text])
        cos_sim = cosine_similarity(vecs[0], vecs[1])[0][0]
    except Exception as e:
        print(f"⚠️ Cosine similarity calculation failed: {str(e)}")
        cos_sim = 0.0

    print(f"📊 BLEU score: {round(bleu_score, 4)}")
    print(f"📊 Cosine similarity: {round(cos_sim, 4)}")
    return bleu_score, cos_sim


In [31]:
# -----------------------------------------------------------------------------
# Module 5: Testing and Full Processing Functions
# -----------------------------------------------------------------------------
import torch

def test_perturbation_on_sample(sample_text: str, ner_model, tokenizer) -> str:
    """
    Tests offset-based perturbation on a single clinical note.
    """
    device = "mps" if torch.backends.mps.is_available() else "cpu"
    ner_model.to(device)
    perturbed_text = perturb_text_offsets(sample_text, ner_model, tokenizer)
    print("========== Test Perturbation ==========")
    print("Original Text:\n", sample_text)
    print("\nPerturbed Text:\n", perturbed_text)
    print("=======================================")
    return perturbed_text

def process_all_notes(df: pd.DataFrame, ner_model, tokenizer) -> None:
    """
    Processes all clinical notes, applies offset-based perturbation,
    evaluates text similarity, and saves detailed outputs to a file.
    Utilizes GPU if available.
    """

    device = "mps" if torch.backends.mps.is_available() else "cpu"
    ner_model.to(device)
    
    bleu_scores = []
    cosine_similarities = []
    total_notes_processed = 0
    vectorizer = TfidfVectorizer()
    
    output_lines = []
    output_lines.append("\n🔄 Processing all notes in the dataset...\n")
    
    for idx, sample_text in enumerate(df['TEXT_PRE']):
        try:
            if not sample_text or len(sample_text.strip()) < 10:
                message = f"⚠️ Skipping note {idx+1}: Text too short or empty"
                print(message)
                output_lines.append(message)
                continue
            total_notes_processed += 1
            perturbed_sample = perturb_text_offsets(sample_text, ner_model, tokenizer)
            # note_message = f"\n🔹 Note {idx+1}:\nOriginal: {sample_text[:200]}...\nPerturbed: {perturbed_sample[:200]}...\n"
            note_message = f"\n🔹 Note {idx+1}:\n"

            print(note_message)
            output_lines.append(note_message)
            
            bleu_score, cos_sim = evaluate_text_similarity(sample_text, perturbed_sample, vectorizer)
            bleu_scores.append(bleu_score)
            cosine_similarities.append(cos_sim)
            
            score_message = f"BLEU score: {round(bleu_score,4)}, Cosine similarity: {round(cos_sim,4)}\n"
            print(score_message)
            output_lines.append(score_message)
            
        except Exception as e:
            err_message = f"⚠️ Error processing note {idx+1}: {str(e)}"
            print(err_message)
            output_lines.append(err_message)
            continue

    summary_lines = []
    summary_lines.append("\n📈 Summary of Results Across All Notes")
    summary_lines.append(f"Total notes processed: {total_notes_processed}/{len(df)}")
    if total_notes_processed > 0:
        avg_bleu = sum(bleu_scores) / len(bleu_scores)
        avg_cos_sim = sum(cosine_similarities) / len(cosine_similarities)
        summary_lines.append(f"Average BLEU score: {round(avg_bleu, 4)}")
        summary_lines.append(f"Average Cosine similarity: {round(avg_cos_sim, 4)}")
    else:
        summary_lines.append("No notes were successfully processed.")
    
    for line in summary_lines:
        print(line)
        output_lines.append(line)
    
    # Save output to file
    with open("perturbation_results.txt", "w") as f:
        f.write("\n".join(output_lines))

In [32]:
# -----------------------------------------------------------------------------
# Module 6: Main Execution Block
# -----------------------------------------------------------------------------
if __name__ == "__main__":
    # Load the trained model from your final checkpoint.
    model_path = "model_v2"  # Use your final saved model folder
    ner_model = AutoModelForTokenClassification.from_pretrained(model_path)
    tokenizer = AutoTokenizer.from_pretrained(model_path)
    
    # Ensure tokenizer max length is set to 512.
    tokenizer.model_max_length = 512

    # Load and preprocess the dataset.
    data_file = "data/SYNTHETIC_DISCHARGE_REPORTS.csv"
    df = load_data(data_file)
    df = preprocess_dataframe(df, text_column="SYNTHETIC_TEXT")

    # Debug: Inspect NER pipeline output on a sample note.
    sample = df['TEXT_PRE'].iloc[0]
    # debug_ner_pipeline(sample, ner_model, tokenizer)

    # Set mode: True for testing a single note; False for full processing.
    TEST_MODE = False
    if TEST_MODE:
        test_perturbation_on_sample(sample, ner_model, tokenizer)
    else:
        process_all_notes(df, ner_model, tokenizer)

Number of notes loaded: 11940


Token indices sequence length is longer than the specified maximum sequence length for this model (516 > 512). Running this sequence through the model will result in indexing errors
Device set to use mps:0
Device set to use mps:0



🔹 Note 1:

📊 BLEU score: 0.9397
📊 Cosine similarity: 0.9903
BLEU score: 0.9397, Cosine similarity: 0.9903



Device set to use mps:0



🔹 Note 2:

📊 BLEU score: 0.9073
📊 Cosine similarity: 0.9631
BLEU score: 0.9073, Cosine similarity: 0.9631



...

📊 BLEU score: 0.9717
📊 Cosine similarity: 0.9842
BLEU score: 0.9717, Cosine similarity: 0.9842


🔹 Note 11936:

📊 BLEU score: 0.9583
📊 Cosine similarity: 0.9894
BLEU score: 0.9583, Cosine similarity: 0.9894



Device set to use mps:0
Device set to use mps:0


⚠️ Error processing note 11937: list index out of range


Device set to use mps:0
Device set to use mps:0



🔹 Note 11938:

📊 BLEU score: 0.9422
📊 Cosine similarity: 0.9522
BLEU score: 0.9422, Cosine similarity: 0.9522


🔹 Note 11939:

📊 BLEU score: 0.9196
📊 Cosine similarity: 0.9616
BLEU score: 0.9196, Cosine similarity: 0.9616


🔹 Note 11940:

📊 BLEU score: 0.9402
📊 Cosine similarity: 0.9639
BLEU score: 0.9402, Cosine similarity: 0.9639


📈 Summary of Results Across All Notes
Total notes processed: 11940/11940
Average BLEU score: 0.9327
Average Cosine similarity: 0.9704
